## initializing the gpu

In [1]:

import torch
print(torch.cuda.is_available())
print(torch.version.cuda)  # Should show the CUDA version PyTorch is using
print(torch.backends.cudnn.version())  # Should
torch.cuda.current_device()

KeyboardInterrupt: 

## Removing BG and Resizing

In [2]:
from rembg import remove
from PIL import Image
import os

input_path = r'D:\shaown\Total project\3D\sample_images\V_pose\12.jpeg'  # input image path
output_path = r'D:/shaown/Total project/3D/sample_images/test.png'  # output image path
resized_path = r'D:/shaown/Total project/3D/results/pifuhd_final/resized/resized_image.png'  # specify filename and extension

input_image = Image.open(input_path)  # load image

# Determine the maximum dimension and calculate the scaling factor
max_dimension = max(input_image.width, input_image.height)
scaling_factor = 512 / max_dimension

# Resize the image with the calculated scaling factor
resized_width = int(input_image.width * scaling_factor)
resized_height = int(input_image.height * scaling_factor)
resized_image = input_image.resize((resized_width, resized_height), Image.LANCZOS)

# Calculate padding for both width and height
padding_width = (512 - resized_width) // 2
padding_height = (512 - resized_height) // 2

# Create a new blank image with size 512x512 and paste the resized image onto it
final_image = Image.new("RGB", (512, 512), (0, 0, 0))
paste_position = (padding_width, padding_height)
final_image.paste(resized_image, paste_position)
final_image.save(resized_path)  # save the resized image

# Remove background
output_image = remove(final_image)

# Save the output image
output_image.save(output_path)


## Height  finding

In [3]:
import subprocess

# Path to the interactive_gui.py script
script_path = "D:/shaown/Total project/3D/apps/interactive_gui.py"

# Run the GUI script as a subprocess
proc = subprocess.Popen(
    ['python', script_path],
    stdout=subprocess.PIPE,
    stderr=subprocess.PIPE,
    text=True
)

# Initialize variables to store the cropped dimensions
cb_width = cb_height = hm_width = hm_height = None
crop_dimensions = ""

while True:
    output = proc.stdout.readline()
    if output == "" and proc.poll() is not None:
        break
    if output:
        crop_dimensions += output.strip() + "\n"
        
        # Debug output to check captured output
        print(f"Captured output: {output.strip()}")

        # Check for checkerboard dimensions output
        if "Checkerboard cropped successfully." in output:
            try:
                # Look for dimensions in the previous output
                dimensions_line = crop_dimensions.splitlines()[-1]  # Get the last line
                if "Height:" in dimensions_line and "Width:" in dimensions_line:
                    dimensions = dimensions_line.split(",")  # Split by comma
                    cb_height = int(dimensions[0].split(":")[1].strip())
                    cb_width = int(dimensions[1].split(":")[1].strip())
                    print(f"Checkerboard dimensions captured: Width = {cb_width}, Height = {cb_height}")
            except (ValueError, IndexError) as e:
                print(f"Error parsing checkerboard dimensions: {e}")

        # Check for human dimensions output
        elif "Human figure cropped successfully." in output:
            try:
                # Look for dimensions in the previous output
                dimensions_line = crop_dimensions.splitlines()[-1]  # Get the last line
                if "Height:" in dimensions_line and "Width:" in dimensions_line:
                    dimensions = dimensions_line.split(",")  # Split by comma
                    hm_height = int(dimensions[0].split(":")[1].strip())
                    hm_width = int(dimensions[1].split(":")[1].strip())
                    print(f"Human figure dimensions captured: Width = {hm_width}, Height = {hm_height}")
            except (ValueError, IndexError) as e:
                print(f"Error parsing human figure dimensions: {e}")

# Communicate any remaining output and errors
stdout, stderr = proc.communicate()

# Check for errors in stderr
if stderr:
    print("Error:", stderr)

# Final output for checkerboard and human dimensions
if cb_width is not None and cb_height is not None:
    print(f"Final Checkerboard dimensions: Width = {cb_width}, Height = {cb_height}")
else:
    print("Checkerboard dimensions not captured.")

if hm_width is not None and hm_height is not None:
    print(f"Final Human figure dimensions: Width = {hm_width}, Height = {hm_height}")
else:
    print("Human figure dimensions not captured.")


Captured output: Saved cropped image: D:/shaown/Total project/3D/results/pifuhd_final/crop_checkerboard\checkerboard_37a0e6cc.png
Captured output: Checkerboard cropped successfully. Height: 96, Width: 57
Checkerboard dimensions captured: Width = 57, Height = 96
Captured output: Saved cropped image: D:/shaown/Total project/3D/results/pifuhd_final/crop_checkerboard\human_3e4c3b42.png
Captured output: Human figure cropped successfully. Height: 678, Width: 159
Human figure dimensions captured: Width = 159, Height = 678
Captured output: Cropping process completed.
Final Checkerboard dimensions: Width = 57, Height = 96
Final Human figure dimensions: Width = 159, Height = 678


In [4]:

cb_height_cm = 25.5
cb_width_cm = 15.5

# Calculate the scale factor
scale_factor = ((cb_height_cm / cb_height) + (cb_width_cm / cb_width)) / 2
cm_hm_height = hm_height * scale_factor -8
cm_hm_height


174.23108552631578

## Finding skeleton

In [ ]:
import cv2
import numpy as np
import torch

from models.with_mobilenet import PoseEstimationWithMobileNet
from modules.load_state import load_state
from modules.keypoints import extract_keypoints, group_keypoints
from modules.pose import Pose
from demo import infer_fast
from google.colab.patches import cv2_imshow

# Load model
net = PoseEstimationWithMobileNet()
checkpoint_path = '/content/lightweight-human-pose-estimation.pytorch/checkpoint_iter_370000.pth'
checkpoint = torch.load(checkpoint_path, map_location='cpu')
load_state(net, checkpoint)
net = net.eval().cpu()  # Stay on CPU in Colab unless you use GPU runtime

# Load image
image_path = '/content/intermediate_10.jpg'
img = cv2.imread(image_path)
assert img is not None, f"Could not load image at {image_path}"
orig_img = img.copy()

# Inference
height_size = 256
stride = 8
upsample_ratio = 4
cpu = True  # Set CPU = True because you’re running on CPU

heatmaps, pafs, scale, pad = infer_fast(net, img, height_size, stride, upsample_ratio, cpu)

# Extract keypoints
num_keypoints = Pose.num_kpts
total_keypoints_num = 0
all_keypoints_by_type = []

for kpt_idx in range(num_keypoints):
    total_keypoints_num += extract_keypoints(heatmaps[:, :, kpt_idx], all_keypoints_by_type, total_keypoints_num)

# Group keypoints into skeletons using PAFs
pose_entries, all_keypoints = group_keypoints(all_keypoints_by_type, pafs)

# Post-process coordinates
for kpt_id in range(all_keypoints.shape[0]):
    all_keypoints[kpt_id, 0] = (all_keypoints[kpt_id, 0] * stride / upsample_ratio - pad[1]) / scale
    all_keypoints[kpt_id, 1] = (all_keypoints[kpt_id, 1] * stride / upsample_ratio - pad[0]) / scale

# Prepare blank canvas for drawing
canvas = orig_img.copy()

# Draw keypoints + skeleton for each detected person
for pose_entry in pose_entries:
    if len(pose_entry) == 0:
        continue

    # Draw keypoints
    for kpt_id in range(num_keypoints):
        if pose_entry[kpt_id] != -1:
            x, y = all_keypoints[int(pose_entry[kpt_id])][:2]
            cv2.circle(canvas, (int(x), int(y)), 5, (0, 255, 255), -1)

    # Draw selected skeleton connections
    BODY_PARTS = [
        (3, 4)  # Example: right elbow to right wrist
    ]

    for part_from, part_to in BODY_PARTS:
        if pose_entry[part_from] != -1 and pose_entry[part_to] != -1:
            x1, y1 = all_keypoints[int(pose_entry[part_from])][:2]
            x2, y2 = all_keypoints[int(pose_entry[part_to])][:2]
            cv2.line(canvas, (int(x1), int(y1)), (int(x2), int(y2)), (0, 255, 0), 2)

# Display the final result
cv2_imshow(canvas)


#checker board width = 15.5 cm

#checker board height 25.5 cm

## Sending the image to PiFuHD

In [5]:
!python -m apps.simple_test

Resuming from  ./checkpoints/pifuhd.pt
test data size:  1
initialize network with normal
initialize network with normal
generate mesh (test) ...
./results/pifuhd_final/recon/result_test_416.obj



100%|██████████| 1/1 [00:18<00:00, 18.65s/it]


## CLeaning Mesh

In [6]:
import trimesh

mesh = trimesh.load('D:/shaown/Total project/3D/results/pifuhd_final/recon/result_test_416.obj')
components = mesh.split(only_watertight=False)
components.sort(key=lambda m: m.volume, reverse=True)
largest_component = components[0]
largest_component.export('D:/shaown/Total project/3D/results/pifuhd_final/recon/cleaned.obj')

print(f"Original mesh had {len(components)} components.")
print("Saved the largest component as 'path_to_output_file.obj'")
mesh1 = trimesh.load('D:/shaown/Total project/3D/results/pifuhd_final/recon/cleaned.obj', force='mesh')

Original mesh had 1127 components.
Saved the largest component as 'path_to_output_file.obj'


In [7]:
mesh1 = trimesh.load(r'D:\shaown\Total project\3D\results\pifuhd_final\recon\cleaned.obj')
mesh1.show()

# creating section

In [8]:
import trimesh
import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import interact
from scipy.interpolate import interp1d
from sklearn.cluster import DBSCAN
from matplotlib.patches import Polygon
from scipy.spatial import ConvexHull

# Load mesh
mesh = mesh1

def calculate_circumference(x, y):
    # Ensure the contour points are closed
    x = np.append(x, x[0])
    y = np.append(y, y[0])
    distances = np.sqrt(np.diff(x)**2 + np.diff(y)**2)
    return np.sum(distances)

def plot_section(plane_origin_y, eps=0.02, min_samples=3):
    plane_normal_z = [0, 0, 1]  # Plane normal along the Z-axis
    plane_normal_y = [0, 1, 0]  # Plane normal along the Y-axis

    # Get minimum y-coordinate of mesh vertices
    min_y = np.min(mesh.vertices[:, 1])

    # Shift plane origin along the y-axis for Z section plot
    plane_origin_z = [mesh.centroid[0], plane_origin_y, mesh.centroid[2]]

    # Compute the section along the Z-axis
    section_z = mesh.section(plane_origin=plane_origin_z,
                             plane_normal=plane_normal_z)

    if section_z is not None:
        section_2d_z, _ = section_z.to_planar()

        # Plot section along Z-axis
        plt.figure(figsize=(18, 6))

        plt.subplot(1, 3, 1)
        plt.scatter(section_2d_z.vertices[:, 0], section_2d_z.vertices[:, 1], s=1)
        plt.title(f"Section at Y = {plane_origin_y} (Z-Axis)")
        plt.xlabel("X")
        plt.ylabel("Y")
        plt.xlim(np.min(section_2d_z.vertices[:, 0]), np.max(section_2d_z.vertices[:, 0]))
        plt.ylim(np.min(section_2d_z.vertices[:, 1]), np.max(section_2d_z.vertices[:, 1]))
        mesh_scale_factor = cm_hm_height /  (np.max(section_2d_z.vertices[:, 1]) -np.min(section_2d_z.vertices[:, 1]))
        # plt.ylim(0,  (np.max(section_2d_z.vertices[:, 0])-np.min(section_2d_z.vertices[:, 0]))*mesh_scale_factor)  # Set lower limit to 0 and upper limit to cm_hm_height


        # Add a horizontal line at the y-position to show cross-section level
        plt.axhline(y=plane_origin_y, color='r', linestyle='--', label='Y-Level')
        plt.legend()

    else:
        print(f"No intersection found for plane at Y = {plane_origin_y}")

    # Now, calculate section along the Y-axis (for variation)
    plane_origin_y_axis = [mesh.centroid[0], plane_origin_y, mesh.centroid[2]]
    section_y = mesh.section(plane_origin=plane_origin_y_axis,
                             plane_normal=plane_normal_y)

    if section_y is not None:
        section_2d_y, _ = section_y.to_planar()

        # Apply DBSCAN to cluster the points
        dbscan = DBSCAN(eps=eps, min_samples=min_samples)
        labels = dbscan.fit_predict(section_2d_y.vertices)

        unique_labels = set(labels)

        # Plot section along Y-axis
        plt.subplot(1, 3, 2)
        plt.title(f"Section at Y = {plane_origin_y} (Y-Axis)")
        plt.xlabel("Z")
        plt.ylabel("X")
        
        # Plot each cluster separately
        for label in unique_labels:
            if label == -1:
                # Black for noise points
                color = 'k'
                marker = 'x'
            else:
                # Different colors for each cluster
                color = plt.cm.Spectral(float(label) / len(unique_labels))
                marker = 'o'
            plt.scatter(section_2d_y.vertices[labels == label, 0], section_2d_y.vertices[labels == label, 1],
                        color=color, label=f'Cluster {label}', s=10, marker=marker)

        plt.xlim(np.min(section_2d_y.vertices[:, 0]), np.max(section_2d_y.vertices[:, 0]))
        plt.ylim(np.min(section_2d_y.vertices[:, 1]), np.max(section_2d_y.vertices[:, 1]))

        # Plot polygons for the clusters in the third subplot
        plt.subplot(1, 3, 3)
        plt.title(f"Contours at Y = {plane_origin_y} (DBSCAN Clusters)")
        plt.xlabel("X")
        plt.ylabel("Y")

        for label in unique_labels:
            if label == -1:
                continue  # Skip noise points

            # Get the points of the cluster
            cluster_points = section_2d_y.vertices[labels == label]

            # Sort points to form a polygon by connecting outer points using ConvexHull
            if len(cluster_points) > 2:  # ConvexHull requires at least 3 points
                hull = ConvexHull(cluster_points)

                # Draw polygon
                polygon = Polygon(cluster_points[hull.vertices], closed=True, fill=None, edgecolor='r')
                plt.gca().add_patch(polygon)
                # Plot points of the polygon
                plt.plot(cluster_points[hull.vertices, 0], cluster_points[hull.vertices, 1], 'ko')

                # Calculate and print circumference using the correct indices for cluster points
                circumference = calculate_circumference(cluster_points[hull.vertices][:, 0], cluster_points[hull.vertices][:, 1]) *mesh_scale_factor/2
                print(f"Circumference of cluster {label} at Y = {plane_origin_y}: {circumference}")


        plt.legend()
    plt.tight_layout()
    plt.show()

# Find the minimum and maximum height of the object in the y-axis
min_y = np.min(mesh.vertices[:, 1])
max_height_y = np.max(mesh.vertices[:, 1])

# Interactively explore different sections along the y-axis with DBSCAN parameters
interact(plot_section, 
         plane_origin_y=(min_y, max_height_y, 0.1), 
         eps=(0.01, 0.1, 0.0001), 
         min_samples=(3, 20, 1))


interactive(children=(FloatSlider(value=-0.013699999999999934, description='plane_origin_y', max=0.8626, min=-…

<function __main__.plot_section(plane_origin_y, eps=0.02, min_samples=3)>

In [9]:
mesh_scale_factor 

NameError: name 'mesh_scale_factor' is not defined

## Final Data

In [311]:
def calculate_height(mesh):
    bounds = mesh.bounds
    height = bounds[1][1] - bounds[0][1]
    return height

mesh = mesh1
components = mesh.split(only_watertight=False)
components.sort(key=lambda m: m.volume, reverse=True)
largest_component = components[0]
current_height = calculate_height(largest_component)
desired_height = cm_hm_height  # replace with your desired height in meters
scaling_factor = desired_height / current_height
largest_component.apply_scale(scaling_factor)
volume = largest_component.volume
volume_m3 = volume * 1e-6  # Convert volume from cubic millimeters to cubic meters
average_human_density = 950  # kg/m^3
mass = volume_m3 * average_human_density
#largest_component.export('path_to_output_file_scaled.obj')

print(f"Original mesh had {len(components)} components.")
print(f"Current height: {current_height} m")
print(f"Scaling factor: {scaling_factor}")
print(f"Volume of the scaled mesh: {volume_m3} m³")
print(f"Mass of the scaled mesh: {mass} kg")
print(f"Saved the scaled component as 'path_to_output_file_scaled.obj'")

Original mesh had 1 components.
Current height: 1.6763 m
Scaling factor: 30.095016322895045
Volume of the scaled mesh: 0.0020380894840860376 m³
Mass of the scaled mesh: 1.9361850098817357 kg
Saved the scaled component as 'path_to_output_file_scaled.obj'


In [312]:
components

[<trimesh.Trimesh(vertices.shape=(109028, 3), faces.shape=(218060, 3), name=`cleaned.obj`)>]